In [6]:
#import numpy as np
import numpy as np
import torch
import cv2

import matplotlib.pyplot as plt
from torch import optim, nn
import torchvision
from torchvision import datasets, models, transforms
import albumentations as A
from albumentations.pytorch import ToTensorV2


print("imports imported")

imports imported


In [7]:
class Identity(nn.Module):
    def __init__(self):
        super(Identity, self).__init__()
        
    def forward(self, x):
        return x

In [8]:
resnet50 = models.resnet50(weights=models.ResNetshotnr0_Weights.DEFAULT)

print(resnetshotnr0)
# Step 2: Modify the model to output features from the layer before the fully connected layer
class ResNetshotnr0Embeddings(nn.Module):
    def __init__(self, original_model, layernr):
        super(ResNetshotnr0Embeddings, self).__init__()
        #print(list(original_model.children())[4 + layernr])
        #print(nn.Sequential(*list(original_model.children())[:4 + shotnr]))
        self.features = nn.Sequential(*list(original_model.children())[:4+layernr])
        #self.features = nn.Sequential(*list(original_model.children())[:-1])  # Exclude the fully connected layer

    def forward(self, x):
        x = self.features(x)
        x = torch.flatten(x, 1)  # Flatten the tensor to (batch_size, 2048)
        return x

# Instantiate the modified model
model = ResNetshotnr0Embeddings(resnetshotnr0, shotnr) # 3 = layer before fully connected one
model.eval()  # Set the model to evaluation mode
print()


ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): Bottleneck(
      (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
      (bn3): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (downsample): Sequential(
        (0): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 

# Test

In [69]:
from sklearn.metrics.pairwise import cosine_similarity,euclidean_distances
from metric_learn import LMNN,NCA
import math

pipe = A.Compose([A.Resize(256,256), A.Normalize(mean=(0.485, 0.456, 0.406), std=(0.229, 0.224, 0.225)), ToTensorV2()])
#pipe = A.Compose([A.Resize(256,256), ToTensorV2()])
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")

m = ResNet50Embeddings(resnet50, 5) # 5 = all without fully ocnnected
m.eval()
m.to(device)

def read_img(path):
    img = cv2.imread(path, cv2.IMREAD_COLOR)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    #plt.imshow(img)

    imgpiped = pipe(image=img)["image"].unsqueeze(0)
    return imgpiped

def compare_embeddings(emb1, emb2, distance_metric):
    #cosi = torch.nn.CosineSimilarity(dim=0) 
    #output = cosine_similarity([emb1.flatten(), emb2.flatten()])
    #output = euclidean_distances([emb1.flatten(), emb2.flatten()], [emb1.flatten(), emb2.flatten()])
    output = distance_metric(emb1, emb2)
    return output

def merge_embeddings(embeddings):
    # todo calc cluster center or similar
    return np.average(embeddings, axis=0)

import os
#embedding_good_1 = m(read_img(f"./data/bottle/test/good/001.png")).detach().numpy()
#embedding_good_2 = m(read_img(f"./data/bottle/test/good/002.png")).detach().numpy()
#embedding_good = merge_embeddings([embedding_good_1, embedding_good_2])
#embedding_contermination_1 = m(read_img(f"./data/bottle/test/contamination/001.png")).detach().numpy()
#embedding_contermination_2 = m(read_img(f"./data/bottle/test/contamination/002.png")).detach().numpy()
#embedding_contermination = merge_embeddings([embedding_contermination_1, embedding_contermination_2])
#embedding_broken_small_1 = m(read_img(f"./data/bottle/test/broken_small/001.png")).detach().numpy()

#embeddings_test = m(read_img(f"./data/bottle/test/contamination/004.png")).detach().numpy()

#score = compare_embeddings(embedding_good_1, embeddings_test)

#def calc_base_emb(t):
#    base_emb_1 = m(read_img(f"./data/bottle/test/{t}/000.png")).detach().numpy()
#    base_emb_2 = m(read_img(f"./data/bottle/test/{t}/001.png")).detach().numpy()
#    base_emb_3 = m(read_img(f"./data/bottle/test/{t}/002.png")).detach().numpy()
#    base_emb_4 = m(read_img(f"./data/bottle/test/{t}/003.png")).detach().numpy()
#    base_emb_5 = m(read_img(f"./data/bottle/test/{t}/004.png")).detach().numpy()
#    base_emb = merge_embeddings([base_emb_1, base_emb_2, base_emb_3, base_emb_4, base_emb_5])
#    return base_emb

MAIN_TYPE="bottle"

def calc_base_emb(t, nr):
    embs = []
    for i in range(nr):
        if t == "good":
            emb = m(read_img(f"./data/{MAIN_TYPE}/train/{t}/{i:03d}.png")).detach().numpy()
        else:
            emb = m(read_img(f"./data/{MAIN_TYPE}/test/{t}/{i:03d}.png")).detach().numpy()
        embs.append(emb)
    base_emb = merge_embeddings(embs)
    return base_emb

shotnr=5
goodnr=5

types = {#"good": calc_base_emb("good", goodnr), 
         #"bad": merge_embeddings([calc_base_emb("broken_large", shotnr), calc_base_emb("broken_small", shotnr), calc_base_emb("contamination", shotnr)]),
                  "broken_large": calc_base_emb("broken_large", shotnr), 
         "broken_small": calc_base_emb("broken_small", shotnr), 
        "contamination": calc_base_emb("contamination", shotnr)
         }


#types = {#"good": calc_base_emb("good", goodnr), 
#         #"bad": merge_embeddings([calc_base_emb("bent_wire", shotnr), calc_base_emb("cable_swap", shotnr), calc_base_emb("combined", shotnr), 
#         #                         calc_base_emb("cut_inner_insulation", shotnr), calc_base_emb("cut_outer_insulation", shotnr), calc_base_emb("missing_cable", shotnr), 
#         #                         calc_base_emb("missing_wire", shotnr), calc_base_emb("poke_insulation", shotnr)]),
#         "bent_wire": calc_base_emb("bent_wire", shotnr),
#         "cable_swap": calc_base_emb("cable_swap", shotnr), 
#         "combined": calc_base_emb("combined", shotnr), 
#         "cut_inner_insulation": calc_base_emb("cut_inner_insulation", shotnr), 
#         "cut_outer_insulation": calc_base_emb("cut_outer_insulation", shotnr), 
#         "missing_cable": calc_base_emb("missing_cable", shotnr), 
#         "missing_wire": calc_base_emb("missing_wire", shotnr), 
#         "poke_insulation": calc_base_emb("poke_insulation", shotnr), 
#         }

# euclidean distance
euclidean_distance_metric = lambda emb1,emb2 : math.pow(euclidean_distances([emb1.flatten(), emb2.flatten()], [emb1.flatten(), emb2.flatten()])[0][1], 2)
# cosine metric
cosine_similarity_metric = lambda emb1,emb2 : cosine_similarity([emb1.flatten(), emb2.flatten()])[0][1]

lmnn = LMNN(n_neighbors=2, learn_rate=1e-3, verbose=True)
#lmnn.fit(data, [0,0,0,1,1,1,2,2,2,3,3,3])

lmnn_similarity_metric = lambda emb1,emb2 : lmnn.get_metric()(emb1.flatten(), emb2.flatten())

Smaller_Better_Metric = False

def test(type):
    predictions = []

    _, _, files = next(os.walk(f"./data/{MAIN_TYPE}/test/{type}/"))
    file_count = len(files)
    for i in range(5,file_count):
        print(".", end="")

        emb = m(read_img(f"./data/{MAIN_TYPE}/test/{type}/{i:03d}.png")).detach().numpy()
        curr_score = .0 if Smaller_Better_Metric else 999999.0
        max_type = ""
        for t in types.keys():
#        for t in ["good", "bad"]:
            score = compare_embeddings(emb, types[t], euclidean_distance_metric)
            
            if Smaller_Better_Metric:
                if score > curr_score:
                    curr_score = score
                    max_type = t
            else:
                if score < curr_score:
                    curr_score = score
                    max_type = t
            pass
        predictions.append(max_type)
        pass
    print()
    return np.mean([x == type for x in predictions])
#    return np.mean([x == ("good" if type == "good" else "bad") for x in predictions])
    pass

accs = []
for t in types.keys():
    if t == "bad":
        continue
    accuracy = test(t)
    print(f"accuracy for {t} = {accuracy}")
    accs.append(accuracy)
print(f"overall accuracy: {np.mean(accs)}")
#print(m)

...............
accuracy for broken_large = 0.6666666666666666
.................
accuracy for broken_small = 0.8823529411764706
................
accuracy for contamination = 0.8125
overall accuracy: 0.7871732026143791


RESNET 50:
Resulsts:

bottle:
jeweils 1,3,5 shots normal
[0.5892857142857143 0.7321428571428571 0.75]

inbalanced - mehr good shots 5,10,15,30 -> alle anderen nur 5
[0.75 0.732 0.696 0.696]

2 ways nur detektieren ob fehlerhaft oder nicht 1,3,5 shots
[0.8395 0.8315 0.8031]

inbalance 2 way 5,10,15,30 -> rest 5
[0.8031 0.81893 0.8336 0.8031]

nur fehlerklasse erkennen 1,3,5
[0.7638 0.7428 0.787]


cable:
jeweils 1,3,5 shots normal
[0.21808 0.43815 0.4321478]

inbalanced - mehr good shots 5,10,15,30 -> alle anderen nur 5
[0.4321478 0.432986 0.42340 0.4464635]

2 ways nur detektieren ob fehlerhaft oder nicht 1,3,5 shots
[0.8592 0.8772 0.8495]

inbalance 2 way 5,10,15,30 -> rest 5
[0.8495 0.8180 0.7460 0.6846]

nur fehlerklasse erkennen 1,3,5
[0.240 0.4740 0.4805]
